In [42]:
!pip install facenet-pytorch
# Imports here
import torch
import torch.functional as F
import torch.nn as nn
import torch.optim as optim
import torchvision
from torch import nn, optim
from torch.optim import lr_scheduler
from torch.autograd import Variable
from torch.utils.data.sampler import SubsetRandomSampler
from torchvision import datasets, models, transforms
from torchvision import datasets, transforms, models
from torch.nn.utils.rnn import pack_padded_sequence, pad_packed_sequence
import json
import numpy as np
import time
import copy
import matplotlib.pyplot as plt
%matplotlib inline
import os,cv2
from facenet_pytorch import MTCNN, InceptionResnetV1
import pandas as pd
#from pylab import rcParams
#rcParams['figure.figsize'] = 20, 10

In [43]:
from google.colab import drive
drive.mount('/content/gdrive')

Drive already mounted at /content/gdrive; to attempt to forcibly remount, call drive.mount("/content/gdrive", force_remount=True).


In [0]:
fer= "./gdrive/My Drive/fer2013/fer2013/fer2013.csv"
ferr= "./gdrive/My Drive/fer2013"

In [45]:
!pip install mxnet

In [47]:
#! /usr/bin/env python3
# -*-coding: utf-8-*-

__author__ = 'Moonkie'

import numpy as np
import cv2
import mxnet as mx
import pandas as pd
import random
import os

curdir = os.path.abspath(os.path.dirname(fer))

def gen_record(csvfile,channel):
    data = pd.read_csv(csvfile,delimiter=',',dtype='a')
    labels = np.array(data['emotion'],np.float)
    # print(labels,'\n',data['emotion'])
        
    imagebuffer = np.array(data['pixels'])
    images = np.array([np.fromstring(image,np.uint8,sep=' ') for image in imagebuffer])
    del imagebuffer
    num_shape = int(np.sqrt(images.shape[-1]))
    images.shape = (images.shape[0],num_shape,num_shape)
    # img=images[0];cv2.imshow('test',img);cv2.waitKey(0);cv2.destroyAllWindow();exit()
    dirs = set(data['Usage'])
    subdirs = set(labels)
    class_dir = {}
    for dr in dirs:
        dest = os.path.join(curdir,dr)
        class_dir[dr] = dest
        if not os.path.exists(dest):
            os.mkdir(dest)
            
    data = zip(labels,images,data['Usage'])
    
    for d in data:
        destdir = os.path.join(class_dir[d[-1]],str(int(d[0])))
        if not os.path.exists(destdir):
            os.mkdir(destdir)
        img = d[1]
        filepath = unique_name(destdir,d[-1])
        print('[^_^] Write image to %s' % filepath)
        if not filepath:
            continue
        sig = cv2.imwrite(filepath,img)
        if not sig:
            print('Error')
            exit(-1)


def unique_name(pardir,prefix,suffix='jpg'):
    filename = '{0}_{1}.{2}'.format(prefix,random.randint(1,10**8),suffix)
    filepath = os.path.join(pardir,filename)
    if not os.path.exists(filepath):
        return filepath
    unique_name(pardir,prefix,suffix)
    


if __name__ == '__main__':
    filename = 'fer2013.csv'
    filename = os.path.join(curdir,filename)
    gen_record(filename,1)
    
    # ##################### test
    # tmp = unique_name('./Training','Training')
    # print(tmp)

[^_^] Write image to /content/gdrive/My Drive/fer2013/fer2013/Training/0/Training_6767793.jpg
[^_^] Write image to /content/gdrive/My Drive/fer2013/fer2013/Training/0/Training_27589833.jpg
[^_^] Write image to /content/gdrive/My Drive/fer2013/fer2013/Training/2/Training_82122925.jpg
[^_^] Write image to /content/gdrive/My Drive/fer2013/fer2013/Training/4/Training_52516219.jpg
[^_^] Write image to /content/gdrive/My Drive/fer2013/fer2013/Training/6/Training_51353315.jpg
[^_^] Write image to /content/gdrive/My Drive/fer2013/fer2013/Training/2/Training_90193562.jpg
[^_^] Write image to /content/gdrive/My Drive/fer2013/fer2013/Training/4/Training_5774644.jpg
[^_^] Write image to /content/gdrive/My Drive/fer2013/fer2013/Training/3/Training_59410655.jpg
[^_^] Write image to /content/gdrive/My Drive/fer2013/fer2013/Training/3/Training_65648004.jpg
[^_^] Write image to /content/gdrive/My Drive/fer2013/fer2013/Training/2/Training_27255793.jpg
[^_^] Write image to /content/gdrive/My Drive/fer201

In [80]:
data_dir = "./gdrive/My Drive/fer2013/fer2013"
#data_dir = 'flower_data'
train_dir = data_dir + '/Training'
valid_dir = data_dir + '/PublicTest'
test_dir = data_dir + '/PrivateTest'
cat_to_name = data_dir + "/cat_to_name.json"
# TODO: Define your transforms for the training and validation sets
data_transforms = {
    'train': transforms.Compose([
        transforms.RandomVerticalFlip(),
        transforms.Resize(160), #160x160
        transforms.RandomResizedCrop(224),
        transforms.ToTensor(),
        transforms.Normalize([0.485, 0.456, 0.406], 
                             [0.229, 0.224, 0.225])
    ]),
    'valid': transforms.Compose([
        transforms.Resize(160),#160x160
        transforms.CenterCrop(224),
        transforms.ToTensor(),
        transforms.Normalize([0.485, 0.456, 0.406], 
                             [0.229, 0.224, 0.225])
    ]),
    'test': transforms.Compose([
        transforms.Resize(160),#160x160
        transforms.CenterCrop(224),
        transforms.ToTensor(),
        transforms.Normalize([0.485, 0.456, 0.406], 
                             [0.229, 0.224, 0.225])
    ])
    }

# TODO: Load the datasets with ImageFolder

dirs = {'train': train_dir, 
        'valid': valid_dir,
        'test': test_dir}

datasets = {x: torchvision.datasets.ImageFolder(dirs[x],   transform=data_transforms[x]) for x in ['train', 'valid', 'test']}

# TODO: Using the image datasets and the trainforms, define the dataloaders

dataloaders = {x: torch.utils.data.DataLoader(datasets[x], batch_size=32, shuffle=True, num_workers=7) for x in ['train', 'valid','test']}

dataset_sizes = {x: len(datasets[x]) 
                              for x in ['train', 'valid','test']}
print(dataset_sizes)

{'train': 28709, 'valid': 3589, 'test': 3589}


In [81]:
import json

with open(cat_to_name, 'r') as f:
    cat_to_name = json.load(f)
print(cat_to_name) 

{'0': 'ANGRY', '1': 'DISGUST', '2': 'FEAR', '3': 'HAPPY', '6': 'NEUTRAL', '4': 'SAD', '5': 'SURPRISE'}


In [82]:
class_names = datasets['train'].classes
print(class_names)

['0', '1', '2', '3', '4', '5', '6']


In [83]:
from facenet_pytorch import MTCNN, InceptionResnetV1

mtcnn = MTCNN()
model = InceptionResnetV1(classify=True, num_classes=7).eval()
model

InceptionResnetV1(
  (conv2d_1a): BasicConv2d(
    (conv): Conv2d(3, 32, kernel_size=(3, 3), stride=(2, 2), bias=False)
    (bn): BatchNorm2d(32, eps=0.001, momentum=0.1, affine=True, track_running_stats=True)
    (relu): ReLU()
  )
  (conv2d_2a): BasicConv2d(
    (conv): Conv2d(32, 32, kernel_size=(3, 3), stride=(1, 1), bias=False)
    (bn): BatchNorm2d(32, eps=0.001, momentum=0.1, affine=True, track_running_stats=True)
    (relu): ReLU()
  )
  (conv2d_2b): BasicConv2d(
    (conv): Conv2d(32, 64, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1), bias=False)
    (bn): BatchNorm2d(64, eps=0.001, momentum=0.1, affine=True, track_running_stats=True)
    (relu): ReLU()
  )
  (maxpool_3a): MaxPool2d(kernel_size=3, stride=2, padding=0, dilation=1, ceil_mode=False)
  (conv2d_3b): BasicConv2d(
    (conv): Conv2d(64, 80, kernel_size=(1, 1), stride=(1, 1), bias=False)
    (bn): BatchNorm2d(80, eps=0.001, momentum=0.1, affine=True, track_running_stats=True)
    (relu): ReLU()
  )
  (conv2d_4a): 

In [0]:
def train_model(model, criteria, optimizer, scheduler = None, epochs=50, device='cuda'):

    since = time.time()
    best_model = copy.deepcopy(model.state_dict())
    
    # initialize tracker for accuracy 
    best_acc = 0 
    TS_loss = pd.DataFrame(np.nan, index = range(1,epochs+1), columns = ['train loss','valid loss'])
    TS_acc = pd.DataFrame(np.nan,index = range(1,epochs+1), columns = ['train acc','valid acc'])
    
    for epoch in range(1,epochs+1):
        print('Epoch {}/{}'.format(epoch, epochs))
        print('-' * 10)
        
        # monitor loss/accuracy
        train_loss_running = 0.0
        valid_loss_running = 0.0
        train_acc_running = 0.0
        valid_acc_running = 0.0

        ###################
        # train the model #
        ###################
        if scheduler:
            scheduler.step()
        model.train() # prep model for training
        
        for data, target in dataloaders['train']:
    
            # Move input and data tensors to the default device
            data, target = data.to(device), target.to(device)
            # clear the gradients of all optimized variables
            optimizer.zero_grad()
            # forward pass: compute predicted outputs by passing inputs to the model
            output = model(data)
            # calculate the batch loss
            loss = criteria(output, target)
            # backward pass: compute gradient of the loss with respect to model parameters
            loss.backward()
            # perform a single optimization step (parameter update)
            optimizer.step()
            # update training loss 
            train_loss_running += loss.item()*data.size(0)
            # accuracy
            _, preds = torch.max(output, 1)
            train_acc_running  += torch.sum(preds == target.data)
            
            del loss

        ######################    
        # validate the model #
        ######################
        model.eval()
        with torch.no_grad():
            for data, target in dataloaders['valid']:
                data, target = data.to(device), target.to(device)
                output = model(data)
                loss = criteria(output, target)
                valid_loss_running += loss.item()*data.size(0)
                
                _, preds = torch.max(output, 1)
                valid_acc_running  += torch.sum(preds == target.data)
                
                del loss
                # Calculate accuracy
                #ps = torch.exp(logps)
                #top_p, top_class = ps.topk(1, dim=1)
                #equals = top_class == labels.view(*top_class.shape)
                #accuracy += torch.mean(equals.type(torch.FloatTensor)).item()

        # statistics
        train_loss = train_loss_running/ dataset_sizes['train']
        valid_loss = valid_loss_running/ dataset_sizes['valid']
        train_acc = train_acc_running.double()/ dataset_sizes['train']
        valid_acc = valid_acc_running.double()/ dataset_sizes['valid']
        
        TS_loss.loc[epoch] = [train_loss, valid_loss]
        TS_acc.loc[epoch] = [(train_acc.cpu().numpy()), (valid_acc.cpu().numpy())]                                         

        # print training/validation statistics 
        print('Train - Loss: {:.4f} Acc: {:.4f}'.format(train_loss, train_acc))
        print('Valid - Loss: {:.4f} Acc: {:.4f}'.format(valid_loss, valid_acc))                                                 
                                                             
        # save model if validation acc has increased
        if valid_acc > best_acc:
            print('Validation Acc increased ({:.4f} --> {:.4f}).  Saving model.'.format(best_acc,valid_acc))
            best_model = copy.deepcopy(model.state_dict())                                                                    
            best_acc = valid_acc
        
        print()
    
    #End
    time_elapsed = time.time() - since
    print('Training complete in {:.0f}m {:.0f}s'.format(time_elapsed // 60, time_elapsed % 60))
    print('Best Valid Acc: {:4f}'.format(best_acc))
                                                   
    TS_loss.plot(title = 'loss')
    TS_acc.plot(title = 'acc')
                                                   
    # load best model weights
    model.load_state_dict(best_model)
    torch.save(model.state_dict(), 'model.pt')
    
    return model

In [0]:
epochs = 15
# freezing the feature part of the pre-trained model 
for param in model.parameters():
    param.requires_grad = True
    


criteria = nn.CrossEntropyLoss()    
    
optimizer = optim.Adam(model.parameters(), lr=1e-2)


scheduler = lr_scheduler.StepLR(optimizer, step_size=4, gamma=0.1)

device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
model.to(device);

model_ft = train_model(model, criteria, optimizer, scheduler, epochs, device)

Epoch 1/15
----------
Train - Loss: 1.8966 Acc: 0.2486
Valid - Loss: 1.8919 Acc: 0.2502
Validation Acc increased (0.0000 --> 0.2502).  Saving model.

Epoch 2/15
----------
Train - Loss: 1.8919 Acc: 0.2522
Valid - Loss: 1.8984 Acc: 0.2137

Epoch 3/15
----------
Train - Loss: 1.8903 Acc: 0.2551
Valid - Loss: 1.9038 Acc: 0.2053

Epoch 4/15
----------
Train - Loss: 1.8878 Acc: 0.2539
Valid - Loss: 1.8968 Acc: 0.2327

Epoch 5/15
----------
Train - Loss: 1.8845 Acc: 0.2598
Valid - Loss: 1.9182 Acc: 0.1900

Epoch 6/15
----------
Train - Loss: 1.8804 Acc: 0.2626
Valid - Loss: 1.8938 Acc: 0.2446

Epoch 7/15
----------
Train - Loss: 1.8729 Acc: 0.2669
Valid - Loss: 1.9055 Acc: 0.2190

Epoch 8/15
----------
Train - Loss: 1.8704 Acc: 0.2716
Valid - Loss: 1.8993 Acc: 0.2282

Epoch 9/15
----------
Train - Loss: 1.8683 Acc: 0.2739
Valid - Loss: 1.8984 Acc: 0.2285

Epoch 10/15
----------
Train - Loss: 1.8680 Acc: 0.2748
Valid - Loss: 1.8933 Acc: 0.2424

Epoch 11/15
----------
Train - Loss: 1.8677 Acc:

In [0]:
modely = models.resnext50_32x4d(pretrained=False)
modely.load_state_dict(torch.load('model.pt'),strict=False)

IncompatibleKeys(missing_keys=['fc.weight', 'fc.bias'], unexpected_keys=['fc.0.weight', 'fc.0.bias', 'fc.2.weight', 'fc.2.bias'])

In [0]:
print(model_ft)


ResNet(
  (conv1): Conv2d(3, 64, kernel_size=(7, 7), stride=(2, 2), padding=(3, 3), bias=False)
  (bn1): BatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
  (relu): ReLU(inplace)
  (maxpool): MaxPool2d(kernel_size=3, stride=2, padding=1, dilation=1, ceil_mode=False)
  (layer1): Sequential(
    (0): Bottleneck(
      (conv1): Conv2d(64, 128, kernel_size=(1, 1), stride=(1, 1), bias=False)
      (bn1): BatchNorm2d(128, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
      (conv2): Conv2d(128, 128, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1), groups=32, bias=False)
      (bn2): BatchNorm2d(128, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
      (conv3): Conv2d(128, 256, kernel_size=(1, 1), stride=(1, 1), bias=False)
      (bn3): BatchNorm2d(256, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
      (relu): ReLU(inplace)
      (downsample): Sequential(
        (0): Conv2d(64, 256, kernel_size=(1, 1), stri

In [0]:
for param in model_ft.parameters():
    param.requires_grad = True

criteria = nn.CrossEntropyLoss()    
    
optimizer = optim.Adam(model_ft.parameters(), lr=1e-5)

device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
model_ft.to(device);

epochs = 70

modelxy = train_model(model_ft, criteria, optimizer,None, epochs, device)

Epoch 1/70
----------
Train - Loss: 1.5397 Acc: 0.3924
Valid - Loss: 1.2957 Acc: 0.5110
Validation Acc increased (0.0000 --> 0.5110).  Saving model.

Epoch 2/70
----------
Train - Loss: 1.4134 Acc: 0.4547
Valid - Loss: 1.1973 Acc: 0.5517
Validation Acc increased (0.5110 --> 0.5517).  Saving model.

Epoch 3/70
----------
Train - Loss: 1.3322 Acc: 0.4889
Valid - Loss: 1.1353 Acc: 0.5712
Validation Acc increased (0.5517 --> 0.5712).  Saving model.

Epoch 4/70
----------
Train - Loss: 1.2825 Acc: 0.5090
Valid - Loss: 1.0980 Acc: 0.5879
Validation Acc increased (0.5712 --> 0.5879).  Saving model.

Epoch 5/70
----------
Train - Loss: 1.2385 Acc: 0.5278
Valid - Loss: 1.0713 Acc: 0.5963
Validation Acc increased (0.5879 --> 0.5963).  Saving model.

Epoch 6/70
----------
Train - Loss: 1.2044 Acc: 0.5424
Valid - Loss: 1.0523 Acc: 0.6096
Validation Acc increased (0.5963 --> 0.6096).  Saving model.

Epoch 7/70
----------
Train - Loss: 1.1689 Acc: 0.5592
Valid - Loss: 1.0399 Acc: 0.6096

Epoch 8/70


KeyboardInterrupt: ignored

In [0]:
# save model as a checkpoint file after every 5 epochs
def save_model_checkpoint(model, optimizer, criteria, epochs):
  model.to('cpu')
  model.class_to_idx = datasets['train'].class_to_idx
  checkpoint = {'input_size': 48*48*1,
                'output_size': 7,
                'model': model,
                'state_dict': model.state_dict(),
                'optimizer_state_dict': optimizer.state_dict(),
                'criterion': criteria,
                'epochs': epochs,
                'class_to_idx': model.class_to_idx}

  path = "/content/gdrive/My Drive/facial_expressions.pth"
  torch.save(checkpoint,path)


# load model function 
def load_checkpoint(filepath):
    checkpoint = torch.load(filepath, map_location='cpu')
    model = checkpoint["model"]
    model.load_state_dict(checkpoint['state_dict'])
    return model

In [0]:
#! /usr/bin/env python3
# -*-coding: utf-8-*-

__author__ = 'Moonkie'

import numpy as np
import cv2
import mxnet as mx
import pandas as pd
import random
import os

curdir = os.path.abspath(os.path.dirname(fer))

def gen_record(csvfile,channel):
    data = pd.read_csv(csvfile,delimiter=',',dtype='a')
    labels = np.array(data['emotion'],np.float)
    # print(labels,'\n',data['emotion'])
        
    imagebuffer = np.array(data['pixels'])
    images = np.array([np.fromstring(image,np.uint8,sep=' ') for image in imagebuffer])
    del imagebuffer
    num_shape = int(np.sqrt(images.shape[-1]))
    images.shape = (images.shape[0],num_shape,num_shape)
    # img=images[0];cv2.imshow('test',img);cv2.waitKey(0);cv2.destroyAllWindow();exit()
    dirs = set(data['Usage'])
    subdirs = set(labels)
    class_dir = {}
    for dr in dirs:
        dest = os.path.join(curdir,dr)
        class_dir[dr] = dest
        if not os.path.exists(dest):
            os.mkdir(dest)
            
    data = zip(labels,images,data['Usage'])
    
    for d in data:
        destdir = os.path.join(class_dir[d[-1]],str(int(d[0])))
        if not os.path.exists(destdir):
            os.mkdir(destdir)
        img = d[1]
        filepath = unique_name(destdir,d[-1])
        print('[^_^] Write image to %s' % filepath)
        if not filepath:
            continue
        sig = cv2.imwrite(filepath,img)
        if not sig:
            print('Error')
            exit(-1)


def unique_name(pardir,prefix,suffix='jpg'):
    filename = '{0}_{1}.{2}'.format(prefix,random.randint(1,10**8),suffix)
    filepath = os.path.join(pardir,filename)
    if not os.path.exists(filepath):
        return filepath
    unique_name(pardir,prefix,suffix)
    


if __name__ == '__main__':
    filename = 'fer2013.csv'
    filename = os.path.join(curdir,filename)
    gen_record(filename,1)
    
    # ##################### test
    # tmp = unique_name('./Training','Training')
    # print(tmp)

[^_^] Write image to /content/gdrive/My Drive/fer2013/fer2013/Training/0/Training_57650482.jpg
[^_^] Write image to /content/gdrive/My Drive/fer2013/fer2013/Training/0/Training_33298324.jpg
[^_^] Write image to /content/gdrive/My Drive/fer2013/fer2013/Training/2/Training_69479871.jpg
[^_^] Write image to /content/gdrive/My Drive/fer2013/fer2013/Training/4/Training_69917638.jpg
[^_^] Write image to /content/gdrive/My Drive/fer2013/fer2013/Training/6/Training_23030614.jpg
[^_^] Write image to /content/gdrive/My Drive/fer2013/fer2013/Training/2/Training_10225233.jpg
[^_^] Write image to /content/gdrive/My Drive/fer2013/fer2013/Training/4/Training_26343213.jpg
[^_^] Write image to /content/gdrive/My Drive/fer2013/fer2013/Training/3/Training_78299539.jpg
[^_^] Write image to /content/gdrive/My Drive/fer2013/fer2013/Training/3/Training_99817089.jpg
[^_^] Write image to /content/gdrive/My Drive/fer2013/fer2013/Training/2/Training_77831900.jpg
[^_^] Write image to /content/gdrive/My Drive/fer2